# Your first scraper
In this project, we will guide you step by step through the process of:

1. creating a self-contained development environment.
1. retrieving some information from an API (a website for computers)
2. leveraging it to scrape a website that does not provide an API
3. saving the output for later processing

Here we query an API for a list of countries and their past leaders. We then extract and sanitize their short bio from Wikipedia. Finally, we save the data to disk.

This task is often the first (coding) step of a datascience project and you will often come back to it in the future.

You will study topics such as *scraping*, *data structures*, *regular expressions*, *concurrency* and *file handling*. We will point out useful resources at the appropriate time. 

Let's dive in!

## Creating a clean environment

Use the [`venv`](https://docs.python.org/3/library/venv.html) command to create a new environment called `wikipedia_scraper_env`.

Activate it.

You will find more info about virtual environments in the course content and on the web.

## API Scraping

### A simple API query
You will start with the basics: how to do a simple request to an [API endpoint](../../2.python/2.python_advanced/05.Scraping/5.apis.ipynb).

You will use the [requests](https://requests.readthedocs.io/en/latest/) external library through the `import` keyword.

NOTE: external libraries need to be installed first. Check their documentation.

Check the [Quickstart](https://requests.readthedocs.io/en/latest/user/quickstart/) section of the Requests documentation to:
1. use the `get()` method to connect to this endpoint: https://country-leaders.onrender.com/status
2. check if the `status_code` is equal to 200, which means OK.
    * if OK, `print()` the `text`` of the response.
    * if not, `print()` the `status_code`. 

Here is the signification of [HTTP status codes](https://en.wikipedia.org/wiki/List_of_HTTP_status_codes).


In [2]:
# import the requests library (1 line)
import requests

# assign the root url (without /status) to the root_url variable for ease of reference (1 line)
root_url = 'https://country-leaders.onrender.com'

# assign the /status endpoint to another variable called status_url (1 line)
status_endpoint = root_url + "/status"

# query the /status endpoint using the get() method and store it in the req variable (1 line)
req = requests.get(status_endpoint)

# check the status_code using a condition and print appropriate messages (4 lines)
if req.status_code == 200:
    print("Status url OK")
else:
    print(f"Status url NOK, code: {status_url}")

Status url OK


### Dealing with JSON

[JSON](https://quickref.me/json) is the preferred format to deal with data over the web. You cannot avoid it so you would better get acquainted.

Connect to another endpoint called `/countries` but this time the API will return data in the JSON format. Check what to do in the Requests [Quickstart](https://requests.readthedocs.io/en/latest/user/quickstart/).


In [3]:
# Set the countries_url variable (1 line)
countries_url = root_url + "/countries"

# query the /countries endpoint using the get() method and store it in the req variable (1 line)
req_countries = requests.get(countries_url)

# Get the JSON content and store it in the countries variable (1 line)
countries = req_countries.json()

# display the request's status code and the countries variable (1 line)
print(req_countries.status_code, countries)

403 {'message': 'The cookie is missing'}


### Cookies anyone?

It looks like the access to this API is restricted...
Query the `/cookie` endpoint and extract the appropriate field to access your cookie.

You will need to use this cookie in each of the following API requests.

In [4]:
# Set the cookie_url variable (1 line)
cookie_url = root_url + '/cookie'

# Query the enpoint, set the cookies variable and display it (2 lines)
req_cookie = requests.get(cookie_url)
cookie = req_cookie.json()
print(cookie)

{'message': 'The cookie has been created'}


Try to query the countries endpoint using the cookie, save the output and print it.

In [7]:
# query the /countries endpoint, assign the output to the countries variable (1 line)

req_countries = requests.get(countries_url, cookies=requests.get(cookie_url).cookies)

# display the countries variable (1 line)
countries = req_countries.json()
print(countries)


['be', 'fr', 'ma', 'ru', 'us']


Chances are the cookie has expired... Thanksfully, you got a nice error message. For now, simply execute the last 2 cells quickly so you get a result.

### Getting the actual data from the API

Query the `/leaders` endpoint.

In [6]:
# Set the leaders_url variable (1 line)
leaders_url = root_url + "/leaders"

# query the /leaders endpoint, assign the output to the leaders variable (1 line)
req_leaders = requests.get(leaders_url, cookies=requests.get(cookie_url).cookies)
leaders = req_leaders.json()
print(leaders)

# display the leaders variable (1 line)


{'message': 'Please specify a country'}


It looks like this endpoint requires additional information in order to return its result. Check the API [*documentation*](https://country-leaders.onrender.com/docs) in your web browser.

Change the query to accept *parameters*. You should know where to find help by now.

In [8]:
# query the /leaders endpoint using cookies and parameters (take any country in countries)
leaders_url = root_url + "/leaders"

# query the /leaders endpoint, assign the output to the leaders variable (1 line)
req_leaders = requests.get(f"{leaders_url}?country=be", cookies=requests.get(cookie_url).cookies)

# assign the output to the leaders variable (1 line)
leaders = req_leaders.json()

# display the leaders variable (1 line)
print(leaders)

[{'id': 'Q12978', 'first_name': 'Guy', 'last_name': 'Verhofstadt', 'birth_date': '1953-04-11', 'death_date': None, 'place_of_birth': 'Dendermonde', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Guy_Verhofstadt', 'start_mandate': '1999-07-12', 'end_mandate': '2008-03-20'}, {'id': 'Q12981', 'first_name': 'Yves', 'last_name': 'Leterme', 'birth_date': '1960-10-06', 'death_date': None, 'place_of_birth': 'Wervik', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Yves_Leterme', 'start_mandate': '2009-11-25', 'end_mandate': '2011-12-06'}, {'id': 'Q12983', 'first_name': 'Herman', 'last_name': 'None', 'birth_date': '1947-10-31', 'death_date': None, 'place_of_birth': 'Etterbeek', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Herman_Van_Rompuy', 'start_mandate': '2008-12-30', 'end_mandate': '2009-11-25'}, {'id': 'Q14989', 'first_name': 'Léon', 'last_name': 'Delacroix', 'birth_date': '1867-12-27', 'death_date': '1929-10-15', 'place_of_birth': 'Saint-Josse-ten-Noode', 'wikipedia_url': 'https://nl

### A sneak peak at the data (finally)

Look inside a few examples. Notice the dictionary keys available for each entry. You have your first example of *structured data*. This data was sanitized for your benefit, meaning it is readily exploitable without modification.

You will also notice there is a Wikipedia link for each entry. You will need to extract additional information there. This will be a case of *semi-structured* data.

The /countries endpoint returns a `list` of several country codes.

You need to loop through this list and query the /leaders endpoint for each one. Save each `json` result in a dictionary called `leaders_per_country`.

In [13]:
# 4 lines
leaders_per_country = {}
for n in range(0, 5):
    req_leaders = requests.get(f"{leaders_url}?country={countries[n]}", cookies=requests.get(cookie_url).cookies)
    leaders = req_leaders.json()
    leaders_per_country[countries[n]] = leaders

print(leaders_per_country)

{'ru': [{'id': 'Q7747', 'first_name': 'Vladimir', 'last_name': 'Putin', 'birth_date': '1952-10-07', 'death_date': None, 'place_of_birth': 'Saint Petersburg', 'wikipedia_url': 'https://ru.wikipedia.org/wiki/%D0%9F%D1%83%D1%82%D0%B8%D0%BD,_%D0%92%D0%BB%D0%B0%D0%B4%D0%B8%D0%BC%D0%B8%D1%80_%D0%92%D0%BB%D0%B0%D0%B4%D0%B8%D0%BC%D0%B8%D1%80%D0%BE%D0%B2%D0%B8%D1%87', 'start_mandate': '2000-05-07', 'end_mandate': '2008-05-07'}, {'id': 'Q23530', 'first_name': 'Dmitry', 'last_name': 'Medvedev', 'birth_date': '1965-09-14', 'death_date': None, 'place_of_birth': 'Saint Petersburg', 'wikipedia_url': 'https://ru.wikipedia.org/wiki/%D0%9C%D0%B5%D0%B4%D0%B2%D0%B5%D0%B4%D0%B5%D0%B2,_%D0%94%D0%BC%D0%B8%D1%82%D1%80%D0%B8%D0%B9_%D0%90%D0%BD%D0%B0%D1%82%D0%BE%D0%BB%D1%8C%D0%B5%D0%B2%D0%B8%D1%87', 'start_mandate': '2008-05-07', 'end_mandate': '2012-05-07'}, {'id': 'Q34453', 'first_name': 'Boris', 'last_name': 'Yeltsin', 'birth_date': '1931-02-01', 'death_date': '2007-04-23', 'place_of_birth': 'Butka', 'wikipe

In [21]:
# or 1 line


https://nl.wikipedia.org/wiki/Guy_Verhofstadt
https://nl.wikipedia.org/wiki/Yves_Leterme
https://nl.wikipedia.org/wiki/Herman_Van_Rompuy
https://nl.wikipedia.org/wiki/L%C3%A9on_Delacroix
https://nl.wikipedia.org/wiki/Henri_Carton_de_Wiart
https://nl.wikipedia.org/wiki/Georges_Theunis
https://nl.wikipedia.org/wiki/Aloys_Van_de_Vyvere
https://nl.wikipedia.org/wiki/Prosper_Poullet
https://nl.wikipedia.org/wiki/Henri_Jaspar
https://nl.wikipedia.org/wiki/Jules_Renkin
https://nl.wikipedia.org/wiki/Paul_van_Zeeland
https://nl.wikipedia.org/wiki/Achiel_Van_Acker
https://nl.wikipedia.org/wiki/Camille_Huysmans
https://nl.wikipedia.org/wiki/Gaston_Eyskens
https://nl.wikipedia.org/wiki/Leo_Tindemans
https://nl.wikipedia.org/wiki/Elio_Di_Rupo
https://nl.wikipedia.org/wiki/Jean-Luc_Dehaene
https://nl.wikipedia.org/wiki/Frans_Schollaert
https://nl.wikipedia.org/wiki/Pieter_de_Decker
https://nl.wikipedia.org/wiki/Paul-Henri_Spaak
https://nl.wikipedia.org/wiki/Auguste_Beernaert
https://nl.wikipedia.org

It is finally time to create a `get_leaders()` function for the above code. You will build on it later-on. This function takes no parameter. Inside it, you will need to:
1. define the urls
2. get the cookies
2. get the countries
3. loop over them and save their leaders in a dictionary
4. return the dictionary

In [9]:
# < 15 lines
import requests
from bs4 import BeautifulSoup

def get_leaders():
    root_url = 'https://country-leaders.onrender.com'
    cookies = requests.get(f"{root_url}/cookie").cookies
    req_countries = requests.get(f"{root_url}/countries", cookies=cookies)
    countries = req_countries.json()
    leaders_per_country = {}
    for country in countries:
        req_leaders = requests.get(f"{root_url}/leaders?country={country}", cookies=cookies)
        leaders = req_leaders.json()
        leaders_per_country[country] = leaders

    return leaders_per_country

Test your function, save the result in the `leaders_per_country` dictionary and check its ouput.

In [10]:
# 2 lines
leaders_per_country = get_leaders()
print(leaders_per_country)

{'be': [{'id': 'Q12978', 'first_name': 'Guy', 'last_name': 'Verhofstadt', 'birth_date': '1953-04-11', 'death_date': None, 'place_of_birth': 'Dendermonde', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Guy_Verhofstadt', 'start_mandate': '1999-07-12', 'end_mandate': '2008-03-20'}, {'id': 'Q12981', 'first_name': 'Yves', 'last_name': 'Leterme', 'birth_date': '1960-10-06', 'death_date': None, 'place_of_birth': 'Wervik', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Yves_Leterme', 'start_mandate': '2009-11-25', 'end_mandate': '2011-12-06'}, {'id': 'Q12983', 'first_name': 'Herman', 'last_name': 'None', 'birth_date': '1947-10-31', 'death_date': None, 'place_of_birth': 'Etterbeek', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Herman_Van_Rompuy', 'start_mandate': '2008-12-30', 'end_mandate': '2009-11-25'}, {'id': 'Q14989', 'first_name': 'Léon', 'last_name': 'Delacroix', 'birth_date': '1867-12-27', 'death_date': '1929-10-15', 'place_of_birth': 'Saint-Josse-ten-Noode', 'wikipedia_url': 'htt

## Extracting data from Wikipedia

Query one of the leaders' Wikipedia urls and display its `text` (not JSON).

In [10]:
# 3 lines
leader_wiki_url = leaders_per_country['fr'][0]['wikipedia_url']
r = requests.get(leader_wiki_url)
text = r.text
pretty_text = BeautifulSoup(text, 'html.parser')
print(pretty_text.prettify())

print(leader_wiki_url)

<!DOCTYPE html>
<html class="client-nojs vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vector-feature-limited-width-content-enabled vector-feature-custom-font-size-clientpref-1 vector-feature-appearance-pinned-clientpref-1 vector-feature-night-mode-enabled skin-theme-clientpref-day vector-toc-available" dir="ltr" lang="fr">
 <head>
  <meta charset="utf-8"/>
  <title>
   François Hollande — Wikipédia
  </title>
  <script>
   (function(){var className="client-js vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-

Ouch! You get the raw HTML code of the webpage. If you try to deal with it without tools, you will be there all night. Instead, use the [beautiful soup 4](https://www.crummy.com/software/BeautifulSoup/bs4/doc/) *external* library. You will find more info about it [here](../../2.python/2.python_advanced/05.Scraping/1.beautifulsoup_basic.ipynb) and [here](../../2.python/2.python_advanced/05.Scraping/2.beautifulsoup_advanced.ipynb)

Using the Quickstart section, start by importing the library and loading the output of your `get_text()` function.

Use the `prettify()` function and print it to take a look. You will start the actual parsing in the next step.

In [11]:
from bs4 import BeautifulSoup

r = requests.get(leader_wiki_url)
soup = BeautifulSoup(r.content, 'html.parser')
print(soup.prettify())

<!DOCTYPE html>
<html class="client-nojs vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vector-feature-limited-width-content-enabled vector-feature-custom-font-size-clientpref-1 vector-feature-appearance-pinned-clientpref-1 vector-feature-night-mode-enabled skin-theme-clientpref-day vector-toc-available" dir="ltr" lang="fr">
 <head>
  <meta charset="utf-8"/>
  <title>
   François Hollande — Wikipédia
  </title>
  <script>
   (function(){var className="client-js vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-

That looks better but you need to extract the right part of the webpage: the text of the first paragraph.

It is a bit tricky because Wikipedia pages slightly differ in structure from one language to the next. We cannot simply get the text for the first HTML paragraph.

You will start by getting all the HTML paragraphs from the HTML source and saving them in the `paragraphs` variable.

Use the documentation or google the appropriate keywords.

In [12]:
# 2 lines
paragraphs = []
for par in soup.find_all("p"):
    paragraphs.append(par.text)
print(paragraphs)

['\n', 'Pour les articles homonymes, voir Hollande (homonymie).\n', '\n', "François Hollande [fʁɑ̃swa ɔlɑ̃d][n 3] Écouter, né le 12 août 1954 à Rouen (Seine-Inférieure), est un haut fonctionnaire et homme d'État français. Il est président de la République française du 15 mai 2012 au 14 mai 2017.\n", "Magistrat à la Cour des comptes et brièvement avocat, il est élu pour la première fois député en 1988. Il exerce la fonction de premier secrétaire du Parti socialiste (PS) de 1997 à 2008, pendant la troisième cohabitation puis dans l'opposition. Au niveau local, il est maire de Tulle de 2001 à 2008 et président du conseil général de Corrèze de 2008 à 2012.\n", "Il est désigné candidat du PS à l'élection présidentielle de 2012 à l'issue d'une primaire à gauche face à Martine Aubry, et élu chef de l'État face au président sortant, Nicolas Sarkozy, avec 51,6\xa0% des suffrages exprimés au second tour.\n", "Sa politique économique connaît un virage social-libéral en 2014, année du «\xa0pacte d

If you try different urls, you might find that the paragraph you want may be at a different index each time.

That is where you need to be clever and ask yourself what would be a reliable way to identify the right index ie. which string matches only the first paragraph whatever the language...

Spend a good 30 minutes on the problem and brainstorm with your fellow learners. If you come out empty handed, ask your coach.

1. Loop over the HTML paragraphs
2. When you have identified the correct one
  * store the [text](https://www.crummy.com/software/BeautifulSoup/bs4/doc/#output) inside the `first_paragraph` variable
  * exit the loop

In [13]:
# <10 lines
bold = []
for par in soup.find_all("p"):
    bold = par.find_all('b')
    if bold != []:
        print(par.text)
        first_paragraph = par.text
        break



François Hollande [fʁɑ̃swa ɔlɑ̃d][n 3] Écouter, né le 12 août 1954 à Rouen (Seine-Inférieure), est un haut fonctionnaire et homme d'État français. Il est président de la République française du 15 mai 2012 au 14 mai 2017.



At this stage, you can create a function to maintain consistency in your code. We will give you its *skeleton*, you will copy the code you wrote and make it work inside a function.

Don't forget to test your function.

In [39]:
# 10 lines
from bs4 import BeautifulSoup

def get_first_paragraph(wikipedia_url):
    r = requests.get(wikipedia_url)
    soup = BeautifulSoup(r.content, 'html.parser')
    print(wikipedia_url) # keep this for the rest of the notebook
#   [insert your code]
    bold = []
    for par in soup.find_all("p"):
        bold = par.find_all('b')
        if bold != []:
            first_paragraph = par.text
            break
    return first_paragraph

In [15]:
# Test: 3 lines
washington = 'https://en.wikipedia.org/wiki/George_Washington'
first_paragraph_washington = get_first_paragraph(washington)
print(first_paragraph_washington)


https://en.wikipedia.org/wiki/George_Washington
George Washington (February 22, 1732 – December 14, 1799) was an American Founding Father, politician, military officer, and farmer who served as the first president of the United States from 1789 to 1797. Appointed by the Second Continental Congress as commander of the Continental Army in 1775, Washington led Patriot forces to victory in the American Revolutionary War and then served as president of the Constitutional Convention in 1787, which drafted the current Constitution of the United States. Washington has thus become commonly known as the "Father of his Country".



### Regular expressions to the rescue

Now that you have extracted the content of the first paragraph, the only thing that remains to finish your Wikipedia scraper is to sanitize the output.

Indeed some Wikipedia references, HTML code, phonetic pronunciation etc. may linger. You might find *regular expressions* handy to get rid of them and obtain pristine text. You will find some useful documentation about regular expressions [here](../../2.python/2.python_advanced/03.Regex/regex.ipynb)

Once you have one of your regex working online, try it in the cell below. 

Hints: 
* Check the `sub()` method documentation.
* Make sure to test urls in different languages. Some may look good but other do not.

In [17]:
# 3 lines



Overwrite the `get_first_paragraph()` function by applying your regex to the first paragraph before returning it.

In [18]:
# 10 lines


Come up with other regexes to capture other patterns and sanitize the outputs completely. Modify your `get_first_paragraph()` function accordingly.

In [19]:
# < 20 lines


## Putting it all together

Let's go back to your `get_leaders()` function and update it with an *inner* loop over each leader. You will query the url provided and extract the first paragraph using the `get_first_paragraph()` function you just finished. You will then update that `leader`'s dictionary and move on to the next one.

Notice, the rest of the code should not change since you modify the leader's data one by one.

In [40]:
# < 20 lines
first_paragraphs = []
print(leaders_per_country)
for key in leaders_per_country:
    for leader in leaders_per_country[key]:
        first_paragraph = get_first_paragraph(leader['wikipedia_url'])
        first_paragraphs.append(first_paragraph)
        leader['first_paragraph'] = first_paragraph

{'be': [{'id': 'Q12978', 'first_name': 'Guy', 'last_name': 'Verhofstadt', 'birth_date': '1953-04-11', 'death_date': None, 'place_of_birth': 'Dendermonde', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Guy_Verhofstadt', 'start_mandate': '1999-07-12', 'end_mandate': '2008-03-20'}, {'id': 'Q12981', 'first_name': 'Yves', 'last_name': 'Leterme', 'birth_date': '1960-10-06', 'death_date': None, 'place_of_birth': 'Wervik', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Yves_Leterme', 'start_mandate': '2009-11-25', 'end_mandate': '2011-12-06'}, {'id': 'Q12983', 'first_name': 'Herman', 'last_name': 'None', 'birth_date': '1947-10-31', 'death_date': None, 'place_of_birth': 'Etterbeek', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Herman_Van_Rompuy', 'start_mandate': '2008-12-30', 'end_mandate': '2009-11-25'}, {'id': 'Q14989', 'first_name': 'Léon', 'last_name': 'Delacroix', 'birth_date': '1867-12-27', 'death_date': '1929-10-15', 'place_of_birth': 'Saint-Josse-ten-Noode', 'wikipedia_url': 'htt

In [41]:
# Check the output of your function (2 lines)
print(leaders_per_country)
for key in leaders_per_country:
    for leader in leaders_per_country[key]:
        print(leader['first_paragraph'])

{'be': [{'id': 'Q12978', 'first_name': 'Guy', 'last_name': 'Verhofstadt', 'birth_date': '1953-04-11', 'death_date': None, 'place_of_birth': 'Dendermonde', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Guy_Verhofstadt', 'start_mandate': '1999-07-12', 'end_mandate': '2008-03-20', 'first_paragraph': 'Guy Maurice Marie-Louise Verhofstadt[5] (uitspraakⓘ) (Dendermonde, 11 april 1953) is een Belgisch politicus voor de Open Vlaamse Liberalen en Democraten (Open Vld). Hij was premier van België van 12 juli 1999 tot 20 maart 2008 in drie regeringen. Hij beëindigde zijn actieve politieke carrière in het Europees Parlement, waar hij van 2009 tot 2019 fractieleider van de Alliantie van Liberalen en Democraten voor Europa (ALDE) was.[6]\n'}, {'id': 'Q12981', 'first_name': 'Yves', 'last_name': 'Leterme', 'birth_date': '1960-10-06', 'death_date': None, 'place_of_birth': 'Wervik', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Yves_Leterme', 'start_mandate': '2009-11-25', 'end_mandate': '2011-12-06'

Does the function crash in the middle of the loop? Chances are the cookies have expired while looping over the leaders.

Modify your function with an *exception* or check if the `status_code` is a cookie error. In either case, get new cookies and query the api again.

If your code did not crash,

In [22]:
# < 25 lines



Check the output of your function again.

In [23]:
# Check the output of your function (1 line)


Well done! It took a while however... Let's speed things up. The main *bottleneck* is the loop. We call on the Wikipedia website many times.

You will use the same *session* to call all the wikipedia pages. Check the *Advanced Usage* section of the Requests module's documentation.

Start by modifying the `get_first_paragraph()` function to accept a session parameter and adjust the `get()` method call.

In [47]:
# < 20 lines

from bs4 import BeautifulSoup

session = requests.Session()

def get_first_paragraph(wikipedia_url):
    r = session.get(wikipedia_url)
    soup = BeautifulSoup(r.content, 'html.parser')
    print(wikipedia_url) # keep this for the rest of the notebook
#   [insert your code]
    bold = []
    for par in soup.find_all("p"):
        bold = par.find_all('b')
        if bold != []:
            first_paragraph = par.text
            break
    return first_paragraph


Modify your `get_leaders()` function to make use of a single session for all the Wikipedia calls.
1. create a `Session` object outside of the loop over countries.
2. pass it to the `get_first_paragraph()` function as an argument.

In [50]:
# <25 lines
from requests import Session
session = requests.Session()

def get_first_paragraph(url: str, session: Session):
    response = session.get(url)
    soup = BeautifulSoup(response.content, 'html.parser')
    bold = []
    for par in soup.find_all("p"):
        bold = par.find_all('b')
        if bold != []:
            first_paragraph = par.text
            break
    return first_paragraph

Test your new functions.



In [52]:
first_paragraphs = []
session = requests.Session()
print(leaders_per_country)
for key in leaders_per_country:
    for leader in leaders_per_country[key]:
        first_paragraph = get_first_paragraph(leader['wikipedia_url'], session)
        first_paragraphs.append(first_paragraph)
        leader['first_paragraph'] = first_paragraph

print(leaders_per_country)

{'be': [{'id': 'Q12978', 'first_name': 'Guy', 'last_name': 'Verhofstadt', 'birth_date': '1953-04-11', 'death_date': None, 'place_of_birth': 'Dendermonde', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Guy_Verhofstadt', 'start_mandate': '1999-07-12', 'end_mandate': '2008-03-20', 'first_paragraph': 'Guy Maurice Marie-Louise Verhofstadt[5] (uitspraakⓘ) (Dendermonde, 11 april 1953) is een Belgisch politicus voor de Open Vlaamse Liberalen en Democraten (Open Vld). Hij was premier van België van 12 juli 1999 tot 20 maart 2008 in drie regeringen. Hij beëindigde zijn actieve politieke carrière in het Europees Parlement, waar hij van 2009 tot 2019 fractieleider van de Alliantie van Liberalen en Democraten voor Europa (ALDE) was.[6]\n'}, {'id': 'Q12981', 'first_name': 'Yves', 'last_name': 'Leterme', 'birth_date': '1960-10-06', 'death_date': None, 'place_of_birth': 'Wervik', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Yves_Leterme', 'start_mandate': '2009-11-25', 'end_mandate': '2011-12-06'

## Saving your hard work

The final step is to save the ``leaders_per_country`` dictionary in the `leaders.json` file using the [json](https://docs.python.org/3/library/json.html) module. Check out the `with` statement.

In [61]:
# 3 lines
import json 
   
   
# Convert and write JSON object to file
with open("leaders.json", "w") as outfile: 
    json.dump(leaders_per_country, outfile)

Make sure the file can be read back. Write the code to read the file. And check the variables are the same.

In [69]:
# 3 lines

# Open and read the JSON file
with open('leaders.json', 'r') as file:
    data = json.load(file)

# Print the data
print(data)

{'be': [{'id': 'Q12978', 'first_name': 'Guy', 'last_name': 'Verhofstadt', 'birth_date': '1953-04-11', 'death_date': None, 'place_of_birth': 'Dendermonde', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Guy_Verhofstadt', 'start_mandate': '1999-07-12', 'end_mandate': '2008-03-20', 'first_paragraph': 'Guy Maurice Marie-Louise Verhofstadt[5] (uitspraakⓘ) (Dendermonde, 11 april 1953) is een Belgisch politicus voor de Open Vlaamse Liberalen en Democraten (Open Vld). Hij was premier van België van 12 juli 1999 tot 20 maart 2008 in drie regeringen. Hij beëindigde zijn actieve politieke carrière in het Europees Parlement, waar hij van 2009 tot 2019 fractieleider van de Alliantie van Liberalen en Democraten voor Europa (ALDE) was.[6]\n'}, {'id': 'Q12981', 'first_name': 'Yves', 'last_name': 'Leterme', 'birth_date': '1960-10-06', 'death_date': None, 'place_of_birth': 'Wervik', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Yves_Leterme', 'start_mandate': '2009-11-25', 'end_mandate': '2011-12-06'

Make a function `save(leaders_per_country)` to call this code easily.

In [66]:
# 3 lines
import json 
   
def save(file):
    # Convert and write JSON object to file
    with open("leaders.json", "w") as outfile: 
        json.dump(file, outfile)

In [68]:
# Call the function (1 line)
save(leaders_per_country)

## Tidy things up in a stand-alone python script

Congratulations! You now have a working scraper! However, your code is scattered throughout this notebook along side the tutorials. Hardly production ready...

Copy and paste what you need in a separate `leaders_scraper.py` file.
Make sure it works by calling `python3 leaders_scraper.py`

## To go further

If you want to practice scraping, you can read this section and tackle the exercise.

You have noticed the API returns very partial results for country leaders. Many are missing. Overwrite the `get_leaders()` function to get its list from Wikipedia and extract their *personal details* from the frame on the side.

Good luck!